# Import modules and packages

In [1]:
import os
import itertools
from collections import Counter
import re


import pandas as pd


import matplotlib.pyplot as plt
import seaborn as sns


import nltk 
from nltk.corpus import stopwords 
from nltk.tokenize import word_tokenize

import pandas as pd 
import numpy as np 
import matplotlib.pyplot as plt 
import json
import gzip


from sklearn.metrics import accuracy_score, f1_score,precision_score,recall_score

nltk.download('stopwords')
nltk.download('punkt')



[nltk_data] Downloading package stopwords to
[nltk_data]     /Users/harryprice/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     /Users/harryprice/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

# Read in file 

In [2]:

def parse(path):
    g = gzip.open('qa_Electronics.json.gz', 'r')
    for l in g:
        yield eval(l)


def parse(path):
    g = gzip.open(path, 'r')
    for l in g:
        yield json.dumps(eval(l))

f = open("output.strict", 'w')
for l in parse("qa_Electronics.json.gz"):
    f.write(l + '\n')


def parse(path):
    g = gzip.open(path, 'rb')
    for l in g:
        yield eval(l)

def getDF(path):
    i = 0
    df = {}
    for d in parse(path):
        df[i] = d
        i += 1
    return pd.DataFrame.from_dict(df, orient='index')

df = getDF('qa_Electronics.json.gz')

# Functions & Relevant Lists

In [3]:
## Cleaning string of any abbreviations / filler words 

to_replace = {"'":'', 'thank you':'','!':'','"':'','#':'','$':'','%':'','&':'',
              '(':'',')':'','*':'','+':'',',':'','-':'','.':'', '/':'',':':'',';':'', '<':'', '=':'', '>':'', '?':'', '@':'',
              '[':'', '\\':'', ']':'', '^':'', '_':'', '`':'', '{':'', '|':'', '}':'', '~':'', '”':'', '“':'',"'":'',
              "£":'','     ':'    ','    ':'   ','   ':'  ', '  ':' ',' don\'t ':' dont ','do not': 'dont','dunno':'dont know','dun kno':'dont know','idk':'i dont know',
              'havnt':'havent','have not':'havent','haven\'t':'havent', 'soz':'sorry','nope':'no','yeah':'yes',' yh ':' yes ', 
              ' yeh ':' yes ',' yea ':' yes ','yup':'yes', ' yep ':' yes ', 'nah':'no', 'srry':'sorry', 'yas':'yes', 'i am': 
              'im',' i\'m ':' im ','hello':'','hi ':' ',' dear ':' ','hey':'','hiya':'','hey there':'','hope this helps':'',
              'heya':'','wassup':'','cheers':'','thanks':''}



## Positive & Negative bigrams and trigrams 
negative_bigrams = [('dont', 'know'), ('dont', 'have'), ('im', 'sorry'),('not','sure'),('not','familiar'),('have','never'),('no', 'idea')]

positive_bigrams = [('work','fine'),('no','problem'),('work','well'),('work','great'),('im','sure'),('not', 'work'),('will', 'work')
                   ,('you', 'need'), ('i', 'would'),('would', 'work')]

negative_trigrams = [('i', 'dont', 'know'), ('i', 'dont', 'have'), ('im', 'not', 'familiar'), ('im', 'not', 'sure')
                    ,('have', 'no', 'idea'),('sorry', 'dont', 'know'),('im', 'not', 'familiar'),('no', 'longer', 'have')]

positive_trigrams = [('will', 'not', 'work')]



## Create list of stopwords and extend it to include punctuation 

stpwrd = nltk.corpus.stopwords.words('english')

punc = '!"#$%&()*+, -./:;<=>?@[\]^_`{|}~”“\''

punc = [x for x in punc]

stpwrd.extend(punc)
stpwrd.extend(["''","'s","x","'m",'1','2','3','4','5','6','7','8','9',"n't"])


## Create list of stopwords and extend it to include punctuation & non-jargon answers

non_jargon = nltk.corpus.stopwords.words('english')

punc = '!"#$%&()*+, -./:;<=>?@[\]^_`{|}~”“\''

punc = [x for x in punc]

non_jargon.extend(punc)
non_jargon.extend(["''","'s","x","'m",'1','2','3','4','5','6','7','8','9',"n't"])



## Extending stopwords list based on commonly occuring, non-jargon words in answers 

non_jargon.extend(['have','not','yes','no','work','use','dont','ha','would','doe','im','need','wa','get','sure','like','good','fit','know','also','great',
                           'one', 'device','well','come','mine','2','time','think','using','go','problem','make','back','unit','see','two',
                           'fine','buy','want','bought','say','may','set','product','really','look','better','long','could','amazon','much','way',
                           'take','3','doesnt','question','new','however','ive','4','help','1','find','support','even','still','year','right',
                           'answer','best','cant','sorry','able','different','havent','thing','little','u','check','put','never','got','since',
                           'hard','believe','without','x','though','side','might','try','price','hope','first','5','pretty','probably','8','small',
                           'another','worked','thats','type','recommend','day','turn','7','around','far','made','purchased','tried','end','didnt',
                           'either','enough','old','purchase','lot','wont','anything','found','came','youre','luck','give','top','item',
                           'many','full','love','easy','going','hold','mean','high','keep','available','30','month','actually','tell','6',
                           '10','us','something','youll','hour','etc','12','second','last','perfectly','working','home','room','difference',
                           'please','looking','le','order','20', 'change','let','place','wouldnt','show','money','cannot','nice', 'id','extra',
                           'always','depends','everything','must','low','left','open','built','big','unless','several','said','maybe',
                           'add','getting','review','wide','point','needed','seems','least','isnt','quite','happy','ear','yet','focus','every',
                           '100','three','away','already','remember','longer','people','search','perfect','send','usually','close','reason',
                           'start'])




## parts of a string that would indicate a hyperlink 
link = ['.com', '.co', 'http', 'www.', '.net', '.gov']


## start has 2545 ish occurences (incase we want to add to list later) 


def clean_abbrevs(string):
    
    ''' Take in a string and replace words in it using the 'to_replace' dictionary.
    Input: String
    Output: String
    '''
    
    for i in range(len(to_replace)):
        string = [string.replace(key,to_replace[key]) for key, value in to_replace.items()][i]
    return string



## Lowercase, and clean abbrevs of q and a, and find number of words in the string. 


def clean_string(question,answer):
    
    '''Clean up strings that are inputted
    Input: 2 strings - a question and an answer
    Method: Make the strings lowercase, clean up any abbreviations in them in order to make the language more 
            uniform, strip any whitespace from the start of end of them, and then calculate a variable, 'y', 
            which is the length of the answer string
    Output: Question, Answer, 'y'
    '''
    
    ## Lowercase the entire string
    answer = answer.lower()
    question = question.lower()

    ## Removing annoying words, abbreviations & punctuation 
    question = clean_abbrevs(question)
    answer = clean_abbrevs(answer)
    
    ## Get rid of whitespace at the start and end 
    answer = answer.strip()
    question = question.strip()
    
    
    ## Get the number of words in the string 
    y = len(answer.split(' '))
    return question, answer, y


                
## Lemmatise a string that is inputted 
def lemmatize_text(text):
    
    ''' Take a string, tokenise it and then lemmatise the words. 
    Input: String
    Output: List
    '''
    return [lemmatizer.lemmatize(w) for w in w_tokenizer.tokenize(text)]







## Function to get the input values
def input_values():
    ''' Function to get input values for our final function.
    No inputs. 
    Outputs: a question, an answer, the question type and the answer type
    '''
    
    
    question = input('Please enter a question: ')
    
    answer = input('Please enter an answer: ')
    
    q_type = input('Please enter either yes/no or open for the type of question: ')
    while q_type not in ['yes/no','open']:
        print('Please enter either yes/no or open for the question type: ')
        q_type = input('Please enter either yes/no or open for the type of question: ')
    
    ans_type = input('Please enter either Y, N, ? or open for the answer type: ')
    while ans_type not in ['Y','N','?','open']:
        print('Please enter an answer type that is either Y, N, ? or open - be careful with capitalisation!')
        ans_type = input('Please enter either Y, N, ? or open for the answer type: ')
    
    return question, answer, q_type, ans_type




def contains_nums(string):
    ''' Function to check if a string contains numbers.
    Input: String 
    Output: Boolean value for if it contains numbers. 
    '''
    
    return bool(re.search('\d+',string))




## Removing non jargon words from answers 

def only_jargon(lst):
    ''' Function for removing non jargon words from a list. Typically a tokenised and lemmatised list of an
        answer would be input: 
        Input: List 
        Output: List after removing non jargon words'''
        
    
    for item in lst:
        if item in non_jargon:
            lst.remove(item)
    
    return lst



## clean_string func but easier to apply to df as only one parameter - can apply to columns more easily. 

def clean_string_df(string):
    
    ''' Function for cleaning a string, altered from the 'clean_string' function to be easier to apply to a column
    of a dataframe. 
    Input: String
    Method: Lowercase the string, clean up any abbreviations, get rid of whitespace. 
    Output: Cleaned string 
    '''
    
    ## Lowercase the entire string
    string = string.lower()

    ## Removing annoying words, abbreviations & punctuation 
    string = clean_abbrevs(string)
    
    ## Get rid of whitespace at the start and end 
    string = string.strip()
    
    
    ## Get the number of words in the string 
    return string


# Final function 

In [73]:
def helpful_or_not(question, answer, question_type, answer_type):
    
    ''' Function to assess whether an answer is helpful or not. 
    Inputs: question (string),answer (string),question_type (string), answer_type (string).
    Method: Perform various checks to gauge its usefulness. 
    Output: Either a 1 (Helpful) or a 0 (Unhelpful)'''

    ## Make the question and answer lowercase to make it easier 
    question,answer,y = clean_string(question,answer)
    
    lemm_answer = lemmatize_text(answer)
    lemm_qs = lemmatize_text(question)

    helpful_indicator = []

    ## Length of the answer - if it is above 24 words (median) then considered helpful 

    if y > 24:
        helpful_indicator.append(2)

    
    ## If an answer is short then we give it a negative point

    if y < 5:
        helpful_indicator.append(-1)

  

    ## Is it a yes/no question & is the answer type yes/no

    if question_type == 'yes/no':
        if answer_type == 'Y' or answer_type == 'N':
            helpful_indicator.append(2)
        else:
            pass



    
    
    ## If answer is just yes or no, and q type is yes/no then classify as helpful 
    
    if question_type == 'yes/no':
        if answer == 'yes' or answer == 'no':
            helpful_indicator.append(2)
        else:
            pass


  ## If the answer contains a link then that can be classified as helpful

    for z in link:
        if z in answer:
            helpful_indicator.append(1)
            break

    ## If numbers in the answer then mark as useful e.g. how long is this cable? answer - 1 metre
    if contains_nums(answer) == True:
        helpful_indicator.append(1)
        


    if answer_type == '?' or answer_type == 'open':

        ## Find answer bigrams
        bigrams = [list(nltk.bigrams(x)) for x in lemm_answer]

        # Find answer trigrams 
        trigrams = [list(nltk.ngrams(x,3)) for x in lemm_answer]

        ## Make list of unhelpful combinations, iterate through, and if there are matches then we score -1 
        for word in negative_bigrams:
            if word in bigrams:
                helpful_indicator.append(-1)
                

        for word in negative_trigrams:
            if word in trigrams:
                helpful_indicator.append(-1)
                
        

    ## Finding common words between question and answer in order to get a measure of similarity/relevance 
    ans_jargon = only_jargon(lemm_answer)
    qs_jargon = only_jargon(lemm_qs)
    
    for x in ans_jargon:
        if x in qs_jargon:
            helpful_indicator.append(1)
            break 
            

        
    ## Returns 1 if the helpful indicator is greater than or equal to 0, other it returns 0           
    if sum(helpful_indicator) >= 0:
        return 1
    else:
        return 0

# Data Cleaning for EDA 

In [5]:
## Made Q's and A's lowercase for testing / EDA 

df['answer'] = df['answer'].str.lower()
df['question'] = df['question'].str.lower()

## Fill na values in answertype with open for open questions 
df['answerType'] = df['answerType'].fillna('open')

## Drop useless columns 
df.drop(columns=['answerTime','unixTime'],axis=1,inplace=True)

In [6]:
# Yes/no q type dataframe 

yes_no = df[df['questionType'] == 'yes/no']

# EDA 

In [7]:
## Experimenting with clean_string function to check it works as we hoped

q,a,y = clean_string("Hello my name is £££ & , , ... don't haven't I'm soz hi ","Hello my name is harry")
print(q)
print(a)
print(y)

my name is  dont havent im sorry
my name is harry
4


In [8]:
# Creating column of tokenised answers

df['tokenised_answer'] = df['answer'].apply(word_tokenize)

In [9]:
# General EDA looking at tokenised answers 

stpwrd = nltk.corpus.stopwords.words('english')

punc = '!"#$%&()*+, -./:;<=>?@[\]^_`{|}~”“\''

punc = [x for x in punc]

stpwrd.extend(punc)
stpwrd.extend(["''","'s","x","'m",'1','2','3','4','5','6','7','8','9',"n't"])


df['tokenised_answer'] = df['tokenised_answer'].apply(lambda x:[words for words in x if words not in stpwrd])


In [10]:
## Attempt at creating wordcloud / word prevalence 
token_counts = Counter()
df['tokenised_answer'].apply(token_counts.update)
#print(token_counts)

0         None
1         None
2         None
3         None
4         None
          ... 
314258    None
314259    None
314260    None
314261    None
314262    None
Name: tokenised_answer, Length: 314263, dtype: object

In [11]:
#df['tokenised_answer_no_stop'] = df['answer'].apply(word_tokenize)

In [12]:
#from nltk.stem import WordNetLemmatizer
#lemmatizer = WordNetLemmatizer()
#df['lemmatized_answer_no_stop'] = [lemmatizer.lemmatize(x) for x in df['answer']]

In [13]:
## Tokeniser and lemmatiser 
w_tokenizer = nltk.tokenize.WhitespaceTokenizer()
lemmatizer = nltk.stem.WordNetLemmatizer()


## Lemmatise text func is at the top 
df['text_lemmatized'] = df.answer.apply(lemmatize_text)

In [14]:
#df['tokenised_answer_no_stop']

In [15]:
#df['text_lemmatized']

In [16]:
## Finding median, general EDA 

# df['len_answer'][df['questionType']=='open-ended'].describe()

In [17]:
## Visually exploring the data to see pattern of answer length 

# temp_df = df[(df['questionType'] == 'open-ended') & (df['len_answer'] < 500)]

# plt.figure(figsize=(15,10),dpi=250)
# sns.histplot(x='len_answer',data=temp_df,bins=50,kde=True)

# Creating a sample for labelled data 


In [18]:
# Create first sample of 200 answers that matches roughly the distribution of answer types 
sample_df = df.sample(n = 200, random_state = 30).copy()

In [19]:
sample_df['questionType'].value_counts()

yes/no        108
open-ended     92
Name: questionType, dtype: int64

In [20]:
sample_df['answerType'].value_counts()

open    92
?       49
Y       41
N       18
Name: answerType, dtype: int64

In [21]:
## Reset index in order to split up answers to label 
sample_df.reset_index(inplace=True, drop=True)

In [22]:
## List of labelled data points for first sample of 200 
helpful=[1,0,1,0,1,0,1,1,1,0,0,0,1,0,1,1,1,1,0,1,1,0,1,1,1,1,1,0,1,1,1,1,1,1,1,1,1,1,1,0,1,1,1,1,1,1,1,0,1,0,0, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1,1,1,0,1,1,1,1,0,0,1,1,1,1,1,1,1,1,0,0,0,0,0,1,1,0,1,0,0,0,0,1,1,0,0,0,0,1,0,1,0,1,1,0,0,1,1,1,1,1,1,1,1,1,1,1,1,1,1,1,1,1,1,0,1,1,0,1,1,1,1,1,1,1,0,1,1,1,1,1,1,1,1,1,1,1,1,1,1,1,1,1,1,1,1,1,1,1,1,1,1]

## Create column for our labels 
sample_df['helpful'] = helpful

In [23]:
## Get predictions off our sample df

sample_df['preds'] = sample_df.apply(lambda x: helpful_or_not(x['question'], x['answer'],x['questionType'], x['answerType']), axis=1)


sample_df['preds'].value_counts()

1    196
0      4
Name: preds, dtype: int64

In [24]:
## Get accuracy, precision, recall & F1 score for model on sample df 

accuracy = accuracy_score(sample_df['helpful'],sample_df['preds'])
recall = recall_score(sample_df['helpful'],sample_df['preds'])
f1 = f1_score(sample_df['helpful'],sample_df['preds'])
precision = precision_score(sample_df['helpful'],sample_df['preds'])

print(accuracy)
print(recall)
print(f1)
print(precision)

0.77
0.9746835443037974
0.8700564971751412
0.7857142857142857


In [25]:
## Explore the errors our model gave us

errors = sample_df[sample_df['helpful'] != sample_df['preds']]

errors[['question','answer']]

question  \
1    battery: does this come with anything to recha...   
3    i have netflix on my tv and a cable box. do i ...   
5    if it comes with a stand and how big the stand...   
9                       does it play the large records   
10   will it fit in/on a sylvania sdvd8791? i curre...   
11   is there a leather case that would go with thi...   
13   has anyone hooked these speakers up to a yamah...   
18          can this computer write (burn) to blu-ray?   
21             will this case fit nook model #bntv600?   
27   does it support samsung google nexus 10 ? sinc...   
39   when using with the ps3 does game play come th...   
47   1. can it play media from any network share (e...   
49   is this thunderbolt version i or ii? this same...   
50                    will it fit the asus transformer   
56   this adapter work in my cannon pixma model mx922?   
63          are these compatible with sharp lc70le845u   
77                    why are different colors cheaper   
95                        does the hedphone jack rust?   
101         how many devices are actually in the box ?   
102  is the base removable to enable using an under...   
104  just want to make sure this has a sd card read...   
107         is it a 32 bit or 64 bit operating system?   
108  hello, i am very interested in buying it. is t...   
116                                         durability   
117  do you need to buy any of the cables for the h...   
118  what do you use to hang it in the car for the ...   
119                   will these fit in 2002 gmc envoe   
120                     can i disarm specific sensors?   
121                             is this a new version?   
124  does the dvd go in on the top or on the side o...   
126         how do get an extra remote for this device   
127  how does this work with speakers that have a k...   
128                   can the camera be solar powered?   
129  where can i buy the film? film on amazon says ...   
132  looking for a pair of walkie talkies to take o...   
133              can you play minecraft on this laptop   
134  if i hook this up using the speaker level inpu...   
135  does this unit have water temp. built in with ...   
137  i ordered this lens today. my order confirmati...   
139                        will this work on an ipad 2   
142  can you charge 18650 at 1000mah or only the 26...   
143                 will this lens work with my d3200?   
162                          what is the weight of it?   
165  does this case fit dell venue 8 (the android v...   
173  how sturdy is the drive? i had a 128gb patriot...   
177  will this work with the 17" macbook pro? does ...   

                                                answer  
1    why not just try to reset it? 1. toggle the ho...  
3    i can't answer your question. i returned the u...  
5    the stand meaning the tripod i'm guessing is a...  
9    nothing on mine worked so i returned it and i ...  
10   i'm not sure... i have an sdvd8706b and it wor...  
11   sorry, i don't know the answer to this questio...  
13   hi peter, i work for a home cinema company and...  
18   excellent question !! someone please answer? a...  
21   i don't know it will fit the orginal nook colo...  
27   the product is very strong and work fine for m...  
39   mines never made it that far. stopped working ...  
47   i have the micca ep600 g2 1080p , so not havin...  
49   i used that cable on my old mac and a brand ne...  
50   what are the dimensions of the asus transforme...  
56   dont know but it should say on the intro which...  
63   can't help,,sorry.they work great on my mitsub...  
77                 trying to get rid of them, i guess.  
95   the unit stopped functioning before i could fi...  
101                                                one  
102  base is removeable though don't know about han...  
104                                        yes it does  
107                                                 64  
108  yes

In [26]:
## Create second sample of 200 to label 

sample_df_2 = df.sample(200,random_state=200)

## Manual labels 
sample_2_preds = [1,1,0,1,1,1,1,1,0,1,1,0,1,1,1,1,0,1,1,1,1,1,1,0,1,1,1,1,1,1,1,1,1,0,1,1,1,1,0,1,0,1,0,1,1,0,1,1,1,1,
           1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
           1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,1,1,1,0,1,1,1,0,0,0,1,1,1,1,1,0,1,0,1,1,1,0,0,0,1,1,1,
           1,1,0,0,1,0,1,1,1,0,1,1,1,1,1,1,1,1,1,1,1,1,1,0,1,1,1,1,1,1,1,1,1,1,1,1,1,1,0,1,1,1,1,1,1,1,1,1,1,1,
           1,1,1,0,1,1,1,1,1,1,1,1,1,1,1,1,0,1,1,1,1,1,1]

## Creating column of the preds 
sample_df_2['preds'] = sample_2_preds

In [27]:
## Second sample df preds, accuracy, recall, precision, F1 scores. 

sample_df_2['func_preds'] = sample_df_2.apply(lambda x: helpful_or_not(x['question'], x['answer'],x['questionType'], x['answerType']), axis=1)
samp_2_accuracy = accuracy_score(sample_df_2['preds'],sample_df_2['func_preds'])
samp_2_recall = recall_score(sample_df_2['preds'],sample_df_2['func_preds'])
samp_2_f1 = f1_score(sample_df_2['preds'],sample_df_2['func_preds'])
samp_2_precision = precision_score(sample_df_2['preds'],sample_df_2['func_preds'])

print(samp_2_accuracy)
print(samp_2_recall)
print(samp_2_f1)
print(samp_2_precision)

0.835
0.9707602339181286
0.9095890410958903
0.8556701030927835


In [28]:
## Looking at bigrams / trigrams in our sample as full df was too big 

#sample_df['bigrams'] = [list(nltk.bigrams(x)) for x in sample_df['tokenised_answer_no_stop']]
sample_df['lemmatized_bigrams'] = [list(nltk.bigrams(x)) for x in sample_df['text_lemmatized']]

In [29]:
## More EDA of different sub dataframes 

yes_no = df[df['questionType']=='yes/no']
ambig_yes_no = yes_no[yes_no['answerType']=='?']

ambig_yes_no['lemmatized_bigrams_ans'] = [list(nltk.bigrams(x)) for x in ambig_yes_no['text_lemmatized']]

<ipython-input-29-f54736ca8a14>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  ambig_yes_no['lemmatized_bigrams_ans'] = [list(nltk.bigrams(x)) for x in ambig_yes_no['text_lemmatized']]


In [30]:
## Editing stopwords list as some words may be relevant in answers e.g. don't have a clue 

stpwrd = nltk.corpus.stopwords.words('english')
stpwrd.extend(punc)
to_remove = ['no', 'nor', 'not','have','haven', "haven't",'don', "don't"]

for s in to_remove:
    if s in stpwrd:
        stpwrd.remove(s)
    else:
        continue
        
print(stpwrd)

['i', 'me', 'my', 'myself', 'we', 'our', 'ours', 'ourselves', 'you', "you're", "you've", "you'll", "you'd", 'your', 'yours', 'yourself', 'yourselves', 'he', 'him', 'his', 'himself', 'she', "she's", 'her', 'hers', 'herself', 'it', "it's", 'its', 'itself', 'they', 'them', 'their', 'theirs', 'themselves', 'what', 'which', 'who', 'whom', 'this', 'that', "that'll", 'these', 'those', 'am', 'is', 'are', 'was', 'were', 'be', 'been', 'being', 'has', 'had', 'having', 'do', 'does', 'did', 'doing', 'a', 'an', 'the', 'and', 'but', 'if', 'or', 'because', 'as', 'until', 'while', 'of', 'at', 'by', 'for', 'with', 'about', 'against', 'between', 'into', 'through', 'during', 'before', 'after', 'above', 'below', 'to', 'from', 'up', 'down', 'in', 'out', 'on', 'off', 'over', 'under', 'again', 'further', 'then', 'once', 'here', 'there', 'when', 'where', 'why', 'how', 'all', 'any', 'both', 'each', 'few', 'more', 'most', 'other', 'some', 'such', 'only', 'own', 'same', 'so', 'than', 'too', 'very', 's', 't', 'can

In [31]:
## More EDA 

ambig_yes_no['tokenised_answer_nostop'] = ambig_yes_no['tokenised_answer'].copy()

<ipython-input-31-5c60ea84d3ef>:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  ambig_yes_no['tokenised_answer_nostop'] = ambig_yes_no['tokenised_answer'].copy()


In [32]:
## Getting rid of stopwords in the column created above

for s in stpwrd:
    if s in ambig_yes_no['tokenised_answer_nostop']:
        ambig_yes_no['tokenised_answer_nostop'].remove(s)
    

In [33]:
## We were planning to make an algorithm to classify answers as Y/N if they were '?' ans type, but lack of time. 

## Work out if '?' ans type is a yes/no or not

## Sort out bigrams for the answers 


## Find most commonly occuring bigrams that might indicate Y/N answer type 


## Classify answers based on that 

In [34]:
# Make df of ambiguous yes/no answers

yes_no = df[df['questionType']=='yes/no']
ambig_yes_no = yes_no[yes_no['answerType']=='?']


# token_counts = Counter()
# ambig_yes_no.iloc[:7500]['lemmatized_bigrams_ans'].apply(token_counts.update)
# print(token_counts)

In [35]:
## Applying func to df column 

ambig_yes_no['clean_ans'] = ambig_yes_no['answer'].apply(clean_string_df)

<ipython-input-35-8d06f8a63ca9>:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  ambig_yes_no['clean_ans'] = ambig_yes_no['answer'].apply(clean_string_df)


In [36]:
# Dropping columns 

# ambig_yes_no.drop(columns=['answer_no_abbrevs','question_no_abbrevs','dunno','len_answer','tokenised_answer_no_stop','text_lemmatized'],axis=1,inplace=True)

# ambig_yes_no.drop(columns=['asin','tokenised_answer'],axis=1,inplace=True)

In [37]:
## A nice post clean tokenise 
ambig_yes_no['tokenised_answer'] = ambig_yes_no['clean_ans'].apply(word_tokenize)

<ipython-input-37-7a5581352d6e>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  ambig_yes_no['tokenised_answer'] = ambig_yes_no['clean_ans'].apply(word_tokenize)


In [38]:
## Lemmatise our cleaned answers

ambig_yes_no['lemmatised_ans'] = ambig_yes_no['clean_ans'].apply(lemmatize_text)

<ipython-input-38-cff75f1413c3>:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  ambig_yes_no['lemmatised_ans'] = ambig_yes_no['clean_ans'].apply(lemmatize_text)


In [39]:
## Remove stopwords 

for s in stpwrd:
    if s in ambig_yes_no['tokenised_answer']:
        ambig_yes_no['tokenised_answer'].remove(s)

In [40]:
## Create a func that can be applied to columns easily to remove stopwords 

def stopwords(x):
    for i in x:
        if i in stpwrd:
            x.remove(i)
        else:
            continue
    
    return x

In [41]:
# Remove stopwords from lemmatised answers 

ambig_yes_no['lemmatised_ans'] = ambig_yes_no['lemmatised_ans'].apply(stopwords)

<ipython-input-41-32eb6741cd83>:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  ambig_yes_no['lemmatised_ans'] = ambig_yes_no['lemmatised_ans'].apply(stopwords)


In [42]:
#ambig_yes_no.drop(columns=['lemm_no_stopwords'],inplace=True)

In [43]:
## Create column with list of tuples of bigrams in lemmatised & cleaned answers 

ambig_yes_no['bigrams'] = [list(nltk.bigrams(x)) for x in ambig_yes_no['lemmatised_ans']]


<ipython-input-43-59d2d973f6fe>:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  ambig_yes_no['bigrams'] = [list(nltk.bigrams(x)) for x in ambig_yes_no['lemmatised_ans']]


In [44]:
## Getting count of bigrams created in cell above 
token_counts = Counter()
ambig_yes_no.iloc[:9000]['bigrams'].apply(token_counts.update)
print(token_counts)

Counter({('dont', 'know'): 596, ('not', 'sure'): 439, ('im', 'not'): 418, ('doe', 'not'): 319, ('not', 'work'): 230, ('i', 'have'): 212, ('dont', 'think'): 206, ('you', 'have'): 205, ('dont', 'have'): 203, ('it', 'work'): 202, ('work', 'fine'): 172, ('i', 'dont'): 169, ('will', 'work'): 167, ('good', 'luck'): 164, ('make', 'sure'): 162, ('would', 'not'): 155, ('the', 'lens'): 151, ('no', 'problem'): 150, ('have', 'no'): 150, ('is', 'not'): 135, ('not', 'have'): 134, ('will', 'not'): 134, ('work', 'well'): 130, ('i', 'would'): 130, ('you', 'can'): 124, ('the', 'camera'): 115, ('use', 'the'): 114, ('you', 'need'): 111, ('work', 'great'): 108, ('will', 'need'): 106, ('have', 'used'): 105, ('have', 'a'): 103, ('is', 'a'): 102, ('dont', 'see'): 100, ('it', 'is'): 98, ('would', 'work'): 98, ('your', 'camera'): 98, ('work', 'the'): 96, ('a', 'good'): 95, ('would', 'have'): 95, ('it', 'not'): 92, ('it', 'doe'): 91, ('to', 'the'): 86, ('you', 'want'): 86, ('it', 'wa'): 84, ('look', 'like'): 83,

In [45]:
## Create column with list of tuples of trigrams in lemmatised & cleaned answers 


ambig_yes_no['trigrams'] = [list(nltk.ngrams(x,3)) for x in ambig_yes_no['lemmatised_ans']]


<ipython-input-45-72dfd2f228d9>:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  ambig_yes_no['trigrams'] = [list(nltk.ngrams(x,3)) for x in ambig_yes_no['lemmatised_ans']]


In [46]:
## Getting count of trigrams created in cell above 


token_counts = Counter()
ambig_yes_no.iloc[:3000]['trigrams'].apply(token_counts.update)
print(token_counts)[100]

Counter({('im', 'not', 'sure'): 94, ('have', 'no', 'idea'): 32, ('doe', 'not', 'have'): 32, ('front', 'the', 'lens'): 20, ('i', 'dont', 'know'): 19, ('im', 'not', 'familiar'): 18, ('sorry', 'dont', 'know'): 17, ('not', 'sure', 'the'): 16, ('dont', 'see', 'not'): 16, ('will', 'not', 'work'): 15, ('dont', 'think', 'will'): 15, ('doe', 'not', 'work'): 14, ('full', 'frame', 'camera'): 14, ('dont', 'know', 'it'): 13, ('the', 'size', 'the'): 13, ('you', 'be', 'fine'): 12, ('dont', 'know', 'sure'): 12, ('lens', 'side', 'the'): 12, ('no', 'longer', 'have'): 12, ('i', 'dont', 'think'): 11, ('filter', 'threaded', 'male'): 11, ('threaded', 'male', 'female'): 11, ('male', 'female', 'one'): 11, ('female', 'one', 'end'): 11, ('one', 'end', 'ha'): 11, ('end', 'ha', '52mm'): 11, ('ha', '52mm', 'male'): 11, ('52mm', 'male', 'thread'): 11, ('male', 'thread', 'camera'): 11, ('thread', 'camera', 'lens'): 11, ('camera', 'lens', 'side'): 11, ('side', 'the', 'end'): 11, ('the', 'end', '52mm'): 11, ('end', '5

TypeError: 'NoneType' object is not subscriptable

In [47]:
# test_lst = []

# ## List of lemmatised words 
# lemm_answer = lemmatize_text('i like lots of ram with my computer audio ')
# lemm_qs = lemmatize_text('i am also a fan of ram and audio')


# # Get rid of all common words, be left with as much specific language / jargon as possible - long list of stopwords

# ans_jargon = only_jargon(lemm_answer)
# qs_jargon = only_jargon(lemm_qs)



# ## if q and a contain similar words then helpful_indicator +1

# for x in ans_jargon:
#         if x in qs_jargon:
#             test_lst.append(1)
            
# print(test_lst)

In [48]:
## EDA to look at common words in cleaned answers to try and identify non-jargon we can remove, 
## in order to assess relevance between Q's amd A's

df['clean_ans'] = df['answer'].apply(clean_string_df)
df['clean_ans'] = df['clean_ans'].apply(lemmatize_text)

token_counts_2 = Counter()
df['clean_ans'].apply(token_counts_2.update)
print(token_counts_2)

Counter({'the': 534759, 'it': 316784, 'a': 301244, 'to': 248338, 'i': 235240, 'and': 214803, 'you': 176894, 'is': 173885, 'for': 120664, 'with': 114592, 'of': 107833, 'on': 102698, 'that': 100865, 'in': 97746, 'have': 97306, 'this': 91097, 'not': 85757, 'but': 76070, 'yes': 72137, 'if': 67420, 'your': 65710, 'my': 64560, 'will': 63203, 'work': 60011, 'can': 59864, 'no': 58353, 'be': 57226, 'are': 54948, 'or': 48247, 'one': 43441, 'use': 42020, 'so': 41637, 'dont': 39713, 'an': 39031, 'ha': 37958, 't': 36240, 'would': 35661, 'from': 35135, 'just': 33854, 'at': 33650, 'camera': 32004, 'there': 29940, 'only': 28558, 'all': 28276, 'doe': 28141, 'im': 26661, 'need': 26463, 'wa': 25962, 'up': 25344, 'get': 24482, 'any': 23862, 'sure': 22019, 'like': 21833, 'should': 21790, 'about': 21689, 'very': 21596, 'good': 21546, 'out': 21288, 'cable': 21229, 'when': 20931, 'fit': 20674, 'battery': 20570, 'had': 20488, 'know': 20035, 'then': 19726, 'also': 19716, 'what': 19691, 'them': 19145, 'do': 1863

# Presentation Examples 

In [79]:
# Unhelpful response 
q1 = 'Does this work with the old Macbook charging cable?'
a1 = "Sorry, I don't know"
qt1 = 'yes/no'
at1 = '?'

helpful_or_not(q1, a1, qt1, at1)

0

In [75]:
#Irrelevant response
q2 = 'Does this work with the old Macbook charging cable?'
a2 = "I like this laptop"
qt2 = 'yes/no'
at2 = '?'

helpful_or_not(q2, a2, qt2, at2)

0

In [76]:
# Semi-helpful response - err on the side of caution 
q3 = 'Does this work with the old Macbook charging cable?'
a3 = "I don't know, but you should try contacting their Amazon store, they are very responsive!"
qt3 = 'yes/no'
at3 = '?'

helpful_or_not(q3, a3, qt3, at3)

1

In [77]:
# Helpful 
q4 = 'Does this work with the old Macbook charging cable?'
a4 = "How old? If it's a charger from 2015 onwards it should work."
qt4 = 'yes/no'
at4 = '?'

helpful_or_not(q4,a4, qt4, at4)

1

In [78]:
# Straightforward and helpful 
q5 = 'Does this work with the old Macbook charging cable?'
a5 = "No it doesn't"
qt5 = 'yes/no'
at5 = 'N'

helpful_or_not(q5,a5,qt5,at5)

1